In [ ]:
# %%capture
# # Installs Unsloth, Xformers (Flash Attention) and all other packages!
!pip install "unsloth[colab-new] @ git+https://github.com/unslothai/unsloth.git" --quiet

# We have to check which Torch version for Xformers (2.3 -> 0.0.27)
from torch import __version__; from packaging.version import Version as V
xformers = "xformers==0.0.27" if V(__version__) < V("2.4.0") else "xformers"
!pip install --no-deps {xformers} "trl<0.9.0" peft accelerate bitsandbytes triton --quiet

!pip install peft --quiet
!pip install --upgrade --no-cache-dir "transformers<4.45.0"  --quiet # Reason: https://github.com/unslothai/unsloth/issues/1061

!pip install -q gradio

  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done


In [ ]:
import gradio as gr
import random
import time
import os
from unsloth import FastLanguageModel
import torch
max_seq_length = 2048 # Choose any! We auto support RoPE Scaling internally!
dtype = None # None for auto detection. Float16 for Tesla T4, V100, Bfloat16 for Ampere+
load_in_4bit = True # Use 4bit quantization to reduce memory usage. Can be False.

huggingface_token = ""

if True:
    from unsloth import FastLanguageModel
    model, tokenizer = FastLanguageModel.from_pretrained(
        model_name = "traversaal-llm-regional-languages/Unsloth_Urdu_Llama3_1_4bit_PF100", # YOUR MODEL YOU USED FOR TRAINING
        max_seq_length = max_seq_length,
        dtype = dtype,
        load_in_4bit = load_in_4bit,
        token = huggingface_token,
    )
    FastLanguageModel.for_inference(model) # Enable native 2x faster inference


alpaca_prompt = """{0}\nInput: {1}\nOutput: """

def generate_text(prompt):
    # Format the prompt with instruction and input, and leave output prompt blank
    formatted_prompt = alpaca_prompt.format(
        "دیئے گئے موضوع کے بارے میں ایک مختصر پیراگراف لکھیں۔",  # instruction
        prompt  # user input
    )

    # Tokenize the prompt and move tensors to GPU
    inputs = tokenizer([formatted_prompt], return_tensors="pt").to("cuda")

    # Generate output from the model
    outputs = model.generate(**inputs, max_new_tokens=500, use_cache=True)

    # Decode the output and remove the instruction + input part
    generated_text = tokenizer.decode(outputs[0], skip_special_tokens=True)

    # Remove the prompt part by splitting on "Output:" and returning only generated part
    result = generated_text.split("Output:")[-1].strip()

    return result

iface = gr.Interface(
    fn=generate_text,
    inputs=gr.Textbox(lines=2, placeholder="Enter your prompt here..."),
    examples=['میں کراچی جانا چاہتا ہوں، وہاں کے کچھ بہترین مقامات کون سے ہیں؟',
              'amazing food locations in Singapore',
              'best activities in London'],
    outputs="text",
    title="Urdu Chatbot - Powered by traversaal-urdu-llama-3.1-8b",
    description="Ask me anything in Urdu!",
)

iface.launch()


🦥 Unsloth: Will patch your computer to enable 2x faster free finetuning.
==((====))==  Unsloth 2024.9.post4: Fast Llama patching. Transformers = 4.44.2.
   \\   /|    GPU: Tesla T4. Max memory: 14.748 GB. Platform = Linux.
O^O/ \_/ \    Pytorch: 2.4.1+cu121. CUDA = 7.5. CUDA Toolkit = 12.1.
\        /    Bfloat16 = FALSE. FA [Xformers = 0.0.28.post1. FA2 = False]
 "-____-"     Free Apache license: http://github.com/unslothai/unsloth
Unsloth: Fast downloading is enabled - ignore downloading bars which are red colored!


Unsloth 2024.9.post4 patched 32 layers with 32 QKV layers, 32 O layers and 32 MLP layers.


Setting queue=True in a Colab notebook requires sharing enabled. Setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. To show errors in colab notebook, set debug=True in launch()
* Running on public URL: https://a0d6ffc6163d5231c4.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)
